## Step 1: Dataset & Storage Setup

**Dataset Source:** [Online Retail II (UCI) - Kaggle](https://www.kaggle.com/datasets/mashlyn/online-retail-ii-uci/data)

**Setup Instructions:**
1. Create a **Volume** within the `lab_2026` catalog.
2. Download the dataset and upload it to the `/.compressed` directory of the created volume.


In [0]:
import os

CATALOG_NAME = 'workspace'
SCHEMA_NAME = 'lab_2026'
VOLUME_DIR = os.path.abspath('/Volumes/{}/{}/'.format(CATALOG_NAME, SCHEMA_NAME))
RAW_DIR = os.path.join(VOLUME_DIR, 'raw')
COMPRESSED_RAW_DIR = os.path.join(RAW_DIR, '.compressed')
if not os.path.exists(COMPRESSED_RAW_DIR):
    raise Exception(f"{COMPRESSED_RAW_DIR} Not Found!")

INPUT_FILE = 'online_retail_II.csv'
compressed_file_path = os.path.join(COMPRESSED_RAW_DIR, INPUT_FILE + '.zip')
dbutils.fs.ls(compressed_file_path)

[FileInfo(path='dbfs:/Volumes/workspace/lab_2026/raw/.compressed/online_retail_II.csv.zip', name='online_retail_II.csv.zip', size=15217139, modificationTime=1766781209000)]

In [0]:
import zipfile

csv_file_path = os.path.join(RAW_DIR)
with zipfile.ZipFile(compressed_file_path, "r") as zip_ref:
    zip_ref.extractall(csv_file_path)
dbutils.fs.ls(csv_file_path)

[FileInfo(path='dbfs:/Volumes/workspace/lab_2026/raw/.compressed/', name='.compressed/', size=0, modificationTime=1766782485612),
 FileInfo(path='dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv', name='online_retail_II.csv', size=94850204, modificationTime=1766782485000)]

In [0]:
spark.read.csv(csv_file_path, header=True, inferSchema=False).limit(5).display()

Invoice StockCode Description Quantity InvoiceDate Price Customer ID Country 489434 85048 15CM CHRISTMAS GLASS BALL 20 LIGHTS 12 2009-12-01 07:45:00 6.95 13085.0 United Kingdom 489434 79323P PINK CHERRY LIGHTS 12 2009-12-01 07:45:00 6.75 13085.0 United Kingdom 489434 79323W WHITE CHERRY LIGHTS 12 2009-12-01 07:45:00 6.75 13085.0 United Kingdom 489434 22041 "RECORD FRAME 7"" SINGLE SIZE " 48 2009-12-01 07:45:00 2.1 13085.0 United Kingdom 489434 21232 STRAWBERRY CERAMIC TRINKET BOX 24 2009-12-01 07:45:00 1.25 13085.0 United Kingdom

## Step 2: The Ingestion Logic

In [0]:
def ingest_raw_to_bronze(source_path, table_name):
    from pyspark.sql import functions as F

    source_df = spark.read.csv(source_path, header=True, inferSchema=False)

    renamed_columns = dict()
    for col in source_df.columns:
        renamed_columns[col] = col.replace(' ', '_').lower()

    raw_df = (
        source_df
        .withColumn('_hash_md5', F.md5(F.concat_ws(',', *source_df.columns)))
        .withColumn('_ingest_timestamp', F.current_timestamp())
        .withColumn('_ingest_author', F.current_user())
        .withColumn('_source_file', F.col("_metadata.file_path"))
        .withColumnsRenamed(renamed_columns)
    )

    (
        raw_df
        .write
        .format('delta')
        .mode('overwrite')
        .option('mergeSchema', True)
        .saveAsTable(table_name)
    )

TABLE_NAME = 'online_retail'
table_name = f'{SCHEMA_NAME}.bronze_{TABLE_NAME}'
ingest_raw_to_bronze(csv_file_path, table_name)
spark.read.table(table_name).display()

invoice stockcode description quantity invoicedate price customer_id country _hash_md5 _ingest_timestamp _ingest_author _source_file 489434 85048 15CM CHRISTMAS GLASS BALL 20 LIGHTS 12 2009-12-01 07:45:00 6.95 13085.0 United Kingdom 8f540e2dceb601d1c14994732a5dec97 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489434 79323P PINK CHERRY LIGHTS 12 2009-12-01 07:45:00 6.75 13085.0 United Kingdom 3a80e4c67de6e819b5daeb79395ab317 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489434 79323W WHITE CHERRY LIGHTS 12 2009-12-01 07:45:00 6.75 13085.0 United Kingdom 5ff842f39a6d8bdb90aa2522efa4072f 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489434 22041 "RECORD FRAME 7"" SINGLE SIZE " 48 2009-12-01 07:45:00 2.1 13085.0 United Kingdom af0d02f57d2e9daee8e5e3d1561359fd 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489434 21232 STRAWBERRY CERAMIC TRINKET BOX 24 2009-12-01 07:45:00 1.25 13085.0 United Kingdom 69145db326f632aa37e590fbded6f0ab 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489434 22064 PINK DOUGHNUT TRINKET POT 24 2009-12-01 07:45:00 1.65 13085.0 United Kingdom d909f1dce88457d0e4723cc8cf7a8d69 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489434 21871 SAVE THE PLANET MUG 24 2009-12-01 07:45:00 1.25 13085.0 United Kingdom f7a1f3e1eb542ef39cf2b255a4c4c0a3 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489434 21523 FANCY FONT HOME SWEET HOME DOORMAT 10 2009-12-01 07:45:00 5.95 13085.0 United Kingdom 61121fde713280adf87973245df2e166 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489435 22350 CAT BOWL 12 2009-12-01 07:46:00 2.55 13085.0 United Kingdom eaf2e356b76cee2872ed7a5d09389dd4 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489435 22349 DOG BOWL , CHASING BALL DESIGN 12 2009-12-01 07:46:00 3.75 13085.0 United Kingdom e3aad9c7dac0fee528d0978f4d1d4ad9 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489435 22195 HEART MEASURING SPOONS LARGE 24 2009-12-01 07:46:00 1.65 13085.0 United Kingdom b5f80e9cc8e222cdbd06bb8d814934d6 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489435 22353 LUNCHBOX WITH CUTLERY FAIRY CAKES 12 2009-12-01 07:46:00 2.55 13085.0 United Kingdom ad09515878510b407c1ac1a3b93ff7cd 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489436 48173C DOOR MAT BLACK FLOCK 10 2009-12-01 09:06:00 5.95 13078.0 United Kingdom b36f5ca093e3e5221da90ba56d85ee86 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489436 21755 LOVE BUILDING BLOCK WORD 18 2009-12-01 09:06:00 5.45 13078.0 United Kingdom 4c96c511e7be6ae02564a38299a04153 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489436 21754 HOME BUILDING BLOCK WORD 3 2009-12-01 09:06:00 5.95 13078.0 United Kingdom cf37b3e9773be28923bda182977ce0d9 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489436 84879 ASSORTED COLOUR BIRD ORNAMENT 16 2009-12-01 09:06:00 1.69 13078.0 United Kingdom 867c28b0a2206e3965ba28ebc5c5f18e 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/lab_2026/raw/online_retail_II.csv 489436 22119 PEACE WOODEN BLOCK LETTERS 3 2009-12-01 09:06:00 6.95 13078.0 United Kingdom 3692cf19366ad32c3bca00c73cd5e696 2025-12-26T20:54:49.150Z gopinadh5g7@sasi.ac.in dbfs:/Volumes/workspace/

In [0]:
%sql

DESCRIBE FORMATTED lab_2026.bronze_online_retail

col_name data_type comment invoice string null stockcode string null description string null quantity string null invoicedate string null price string null customer_id string null country string null _hash_md5 string null _ingest_timestamp timestamp null _ingest_author string null _source_file string null # Delta Statistics Columns Column Names quantity, customer_id, description, price, country, invoice, _ingest_author, stockcode, invoicedate, _source_file, _ingest_timestamp, _hash_md5 Column Selection Method first-32 # Detailed Table Information Catalog workspace Database lab_2026 Table bronze_online_retail Created Time Fri Dec 26 20:41:14 UTC 2025 Last Access UNKNOWN Created By Spark Statistics 41105496 bytes, 1067371 rows Type MANAGED Location Provider delta Owner gopinadh5g7@sasi.ac.in Is_managed_location true Predictive Optimization ENABLE (inherited from METASTORE metastore_aws_us_east_2) Table Properties [delta.enableDeletionVectors=true,delta.feature.appendOnly=supported,delta.feature.deletionVectors=supported,delta.feature.invariants=supported,delta.minReaderVersion=3,delta.minWriterVersion=7]

In [0]:
%sql

DESCRIBE HISTORY lab_2026.bronze_online_retail

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 3 2025-12-26T20:54:53.000Z 76410191890103 gopinadh5g7@sasi.ac.in CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(2884203686590536) 1226-191418-v62hfpy0-v2n 2 WriteSerializable false Map(numFiles -> 2, numRemovedFiles -> 2, numRemovedBytes -> 41105496, numDeletionVectorsRemoved -> 0, numOutputRows -> 1067371, numOutputBytes -> 41105496) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 2 2025-12-26T20:41:37.000Z 76410191890103 gopinadh5g7@sasi.ac.in CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(2884203686590536) 1226-191418-v62hfpy0-v2n 1 WriteSerializable false Map(numFiles -> 2, numRemovedFiles -> 2, numRemovedBytes -> 41105496, numDeletionVectorsRemoved -> 0, numOutputRows -> 1067371, numOutputBytes -> 41105496) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 1 2025-12-26T20:41:28.000Z 76410191890103 gopinadh5g7@sasi.ac.in CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(2884203686590536) 1226-191418-v62hfpy0-v2n 0 WriteSerializable false Map(numFiles -> 2, numRemovedFiles -> 2, numRemovedBytes -> 41105496, numDeletionVectorsRemoved -> 0, numOutputRows -> 1067371, numOutputBytes -> 41105496) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13 0 2025-12-26T20:41:15.000Z 76410191890103 gopinadh5g7@sasi.ac.in CREATE OR REPLACE TABLE AS SELECT Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> true, properties -> {"delta.enableDeletionVectors":"true"}, statsOnLoad -> true) null List(2884203686590536) 1226-191418-v62hfpy0-v2n null WriteSerializable false Map(numFiles -> 2, numRemovedFiles -> 0, numRemovedBytes -> 0, numDeletionVectorsRemoved -> 0, numOutputRows -> 1067371, numOutputBytes -> 41105496) null Databricks-Runtime/17.3.x-aarch64-photon-scala2.13